# Gereral Imports

**Importing all libraries**

In [117]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

from functools import reduce
import gc
import geopandas as gpd
import cbsodata
from owslib.wfs import WebFeatureService

In [118]:
# Download geboortecijfers en verwijder spaties uit regiocodes
data_gezondheidsmonitor = pd.DataFrame(cbsodata.get_data('85012NED'))

In [119]:
# Verkijg alle leeftijds categorieën (aangezien deze niet specifiek genoeg zijn)
data_gezondheidsmonitor = data_gezondheidsmonitor[data_gezondheidsmonitor['Leeftijd'] == 'Totaal']

# Verkijg enkel de marges
data_gezondheidsmonitor = data_gezondheidsmonitor[data_gezondheidsmonitor['Marges'] == 'Waarde']

In [120]:
# Leeftijd selectie of totaal
data_gezondheidsmonitor[['RegioS', 'Ondergewicht_7',
       'NormaalGewicht_8', 'Overgewicht_9', 'MatigOvergewicht_10',
       'ErnstigOvergewichtObesitas_11']]

RegioS  Ondergewicht_7  NormaalGewicht_8  \
0                        Nederland             1.7              48.8   
1             Noord-Nederland (LD)             1.6              47.0   
2              Oost-Nederland (LD)             1.5              47.3   
3              West-Nederland (LD)             1.9              50.8   
4              Zuid-Nederland (LD)             1.7              46.9   
..                             ...             ...               ...   
393         GGD Limburg-Noord (GG)             1.5              46.1   
394          GGD Zuid-Limburg (GG)             1.9              44.2   
395            GGD Haaglanden (GG)             2.0              51.1   
396               GGD Fryslân (GG)             1.6              47.4   
397  GGD Zaanstreek/Waterland (GG)             1.3              46.5   

     Overgewicht_9  MatigOvergewicht_10  ErnstigOvergewichtObesitas_11  
0             49.4                 34.8                           14.7  
1             51.4                 36.0                           15.4  
2             51.2                 35.8                           15.4  
3             47.4                 33.6                           13.8  
4             51.5                 35.8                           15.7  
..             ...                  ...                            ...  
393           52.4                 36.9                           15.6  
394           54.0                 36.2                           17.8  
395           46.9                 33.2                           13.8  
396           51.0                 36.4                           14.5  
397           52.2                 36.2                           16.0  

[398 rows x 6 columns]

In [121]:
geodata_url = 'https://service.pdok.nl/cbs/gebiedsindelingen/2017/wfs/v1_0'
wfs = WebFeatureService(geodata_url, version='2.0.0')

# Controleer de beschikbare lagen
print(wfs.contents)

{'gebiedsindelingen:arbeidsmarktregio_gegeneraliseerd': <owslib.feature.wfs200.ContentMetadata object at 0x000001DD271A3D60>, 'gebiedsindelingen:arbeidsmarktregio_labelpoint': <owslib.feature.wfs200.ContentMetadata object at 0x000001DD271A3B80>, 'gebiedsindelingen:arrondissementsgebied_gegeneraliseerd': <owslib.feature.wfs200.ContentMetadata object at 0x000001DD271A3FA0>, 'gebiedsindelingen:arrondissementsgebied_labelpoint': <owslib.feature.wfs200.ContentMetadata object at 0x000001DD271A3EE0>, 'gebiedsindelingen:buurt_gegeneraliseerd': <owslib.feature.wfs200.ContentMetadata object at 0x000001DD271A3D00>, 'gebiedsindelingen:buurt_labelpoint': <owslib.feature.wfs200.ContentMetadata object at 0x000001DD271A3B20>, 'gebiedsindelingen:coropgebied_gegeneraliseerd': <owslib.feature.wfs200.ContentMetadata object at 0x000001DD271A3940>, 'gebiedsindelingen:coropgebied_labelpoint': <owslib.feature.wfs200.ContentMetadata object at 0x000001DD271A3760>, 'gebiedsindelingen:coropplusgebied_gegeneralise

In [122]:
# Kies de gewenste laag
laagnaam = 'gemeente_gegeneraliseerd'

# Haal de gegevens op van de gekozen laag
response = wfs.getfeature(typename=laagnaam, outputFormat='json')
data = response.read().decode('utf-8')

# Converteer de ontvangen gegevens naar een GeoDataFrame
gemeentegrenzen = gpd.read_file(data)

In [123]:
# Koppel CBS-data aan geodata met regiocodes
gemeentegrenzen = pd.merge(gemeentegrenzen,
                           data_gezondheidsmonitor,
                           left_on = "statnaam", 
                           right_on = "RegioS", 
                           how="left")

In [124]:
gemeentegrenzen.columns

Index(['id', 'statcode', 'statnaam', 'jrstatcode', 'rubriek', 'geometry', 'ID',
       'Leeftijd', 'Marges', 'RegioS', 'ErvarenGezondheidGoedZeerGoed_1',
       'EenOfMeerLangdurigeAandoeningen_2',
       'EenOfMeerLichamelijkeBeperkingen_3', 'BeperkingInHoren_4',
       'BeperkingInZien_5', 'BeperkingInBewegen_6', 'Ondergewicht_7',
       'NormaalGewicht_8', 'Overgewicht_9', 'MatigOvergewicht_10',
       'ErnstigOvergewichtObesitas_11', 'VoldoetAanBeweegrichtlijn_12',
       'WekelijksSporter_13', 'Mantelzorger_14',
       'ZwaarBelasteMantelzorgers_15', 'UrenMantelzorgPerWeek_16', 'Rokers_17',
       'VoldoetAanRichtlijnAlcoholgebruik_18', 'ZwareDrinker_19',
       'OvermatigDrinker_20'],
      dtype='object')

In [125]:
# Drop unnecessary columns 
gemeentegrenzen.drop(columns=['id', 'statcode', 'jrstatcode', 'rubriek', 'ID', 'Leeftijd', 'Marges', 'RegioS'], inplace=True)

# Rename columns
gemeentegrenzen = gemeentegrenzen.rename(columns=lambda x: x.split("_")[0])

In [126]:
# pip install folium matplotlib mapclassify

# Interactive plot
gemeentegrenzen.explore(
    column="ErnstigOvergewichtObesitas",
    tooltip=["ErnstigOvergewichtObesitas", 'MatigOvergewicht', "Overgewicht", "statnaam"],
    popup=True,
    tiles="",
    cmap="OrRd",
    style_kwds=dict(color="black"), 
)

In [128]:
# Interactive plot
gemeentegrenzen.explore(
    column="MatigOvergewicht",
    tooltip=["ErnstigOvergewichtObesitas", 'MatigOvergewicht', "Overgewicht", "statnaam"],
    popup=True,
    tiles="",
    cmap="OrRd",
    style_kwds=dict(color="black"), 
)

In [129]:
# Interactive plot
gemeentegrenzen.explore(
    column="Overgewicht",
    tooltip=["ErnstigOvergewichtObesitas", 'MatigOvergewicht', "Overgewicht", "statnaam"],
    popup=True,
    tiles="",
    cmap="OrRd",
    style_kwds=dict(color="black"), 
)